In [ ]:
"""
include ffmpeg.exe in working dir (if not on path)
    get ffmpeg.exe here: http://www.ffmpeg.org/download.html
"""

In [1]:
## download mp3 from youtube
from __future__ import unicode_literals
import youtube_dl
import ffmpeg
import subprocess

import glob
import pandas as pd

import numpy as np
import matplotlib.pyplot as plt
import librosa.display
import librosa
# https://github.com/nageshsinghc4/Audio-Data-Analysis-Using-Deep-Learning
# audio data analysis
# https://www.theaidream.com/post/audio-data-analysis-using-deep-learning-with-python-part-1

# youtube_dl options
ydl_opts = {
    'format': 'bestaudio/best',
    'outtmpl': 'downloads/%(id)s-%(title)s.%(ext)s', #file save loc
    'postprocessors': [{
        'key': 'FFmpegExtractAudio',
        'preferredcodec': 'mp3',
        'preferredquality': '192',
    }],
}

"""
# export file from youtube
with youtube_dl.YoutubeDL(ydl_opts) as ydl:
    ydl.download(['http://www.youtube.com/watch?v=BaW_jenozKc'])
"""

"\n# export file from youtube\nwith youtube_dl.YoutubeDL(ydl_opts) as ydl:\n    ydl.download(['http://www.youtube.com/watch?v=BaW_jenozKc'])\n"

In [2]:
## convert music file format, if needed
import pydub
inFile = 'test.m4a'
outFile = 'test.mp3'
sound = pydub.AudioSegment.from_file(inFile)
sound.export(outFile, format="mp3")

In [36]:
## test audio Lists
songList_Astley = ['https://www.youtube.com/watch?v=dQw4w9WgXcQ&ab_channel=RickAstley' #official
            ,'https://www.youtube.com/watch?v=34Ig3X59_qA&ab_channel=DopeLyrics' #remaster
            ,'https://www.youtube.com/watch?v=o-YBDTqX_ZU&ab_channel=MusRest' #remaster2
            ,'https://www.youtube.com/watch?v=dQw4w9WgXcQ&ab_channel=RickAstley' #official
            ,'https://www.youtube.com/watch?v=oHg5SJYRHA0&ab_channel=cotter548' #poor
            ,'https://www.youtube.com/watch?v=iik25wqIuFo&ab_channel=Rickroll%2Cbutwithadifferentlink' #short
            ,'https://www.youtube.com/watch?v=1P5yyeeYF9o&ab_channel=PinkerHumor' #voiceCrack
            ,'https://www.youtube.com/watch?v=8VFzHYtOARw&ab_channel=TalkingNonsense' #bassBoost
           ]

songList_SmashMouth = ['https://www.youtube.com/watch?v=L_jWHffIx5E&ab_channel=SmashMouthVEVO' #music video
            ,'https://www.youtube.com/watch?v=LYG7sMtb6u8&ab_channel=%E2%99%AAFenderGibsonSounds%E2%99%AA' #hq #win
            ,'https://www.youtube.com/watch?v=aT5JaB5agSE&ab_channel=BUGGLyrics' #delay then hq
            ,'https://www.youtube.com/watch?v=8sFXsP71wfA&ab_channel=Broccaloo' #bad
            ,'https://www.youtube.com/watch?v=QJJWmBlONIQ&ab_channel=GeekHeavy' #kermit
            ,'https://www.youtube.com/watch?v=-UxD1FObOH4&ab_channel=DeLoreanAustria' #instrumental
            ,'https://www.youtube.com/watch?v=8gsy8KKjjFI&ab_channel=Sway%27sCreepyLife' #live
            ,'https://www.youtube.com/watch?v=fGgOzxg2lRI&ab_channel=BrockBaker' #cartoon
            ]

In [37]:
## download songList
with youtube_dl.YoutubeDL(ydl_opts) as ydl:
    ydl.download(songList_SmashMouth)
print("----------------COMPLETE----------------")

[youtube] L_jWHffIx5E: Downloading webpage
[download] Destination: downloads\L_jWHffIx5E-Smash Mouth - All Star (Official Music Video).m4a
[download] 100% of 3.65MiB in 00:54                  
[ffmpeg] Correcting container in "downloads\L_jWHffIx5E-Smash Mouth - All Star (Official Music Video).m4a"
[ffmpeg] Destination: downloads\L_jWHffIx5E-Smash Mouth - All Star (Official Music Video).mp3
Deleting original file downloads\L_jWHffIx5E-Smash Mouth - All Star (Official Music Video).m4a (pass -k to keep)
[youtube] LYG7sMtb6u8: Downloading webpage
[download] Destination: downloads\LYG7sMtb6u8-Smash Mouth _ All Star (HQ).m4a
[download] 100% of 3.12MiB in 01:12                 
[ffmpeg] Correcting container in "downloads\LYG7sMtb6u8-Smash Mouth _ All Star (HQ).m4a"
[ffmpeg] Destination: downloads\LYG7sMtb6u8-Smash Mouth _ All Star (HQ).mp3
Deleting original file downloads\LYG7sMtb6u8-Smash Mouth _ All Star (HQ).m4a (pass -k to keep)
[youtube] aT5JaB5agSE: Downloading webpage
[download] Desti

In [49]:
## Variables
# enter base folder that holds mp3 files to compare
#baseFolder = r'C:\Lighthouse\Python\Hackathons\2022.2 misc\downloads\Astley'
baseFolder = r'C:\Lighthouse\Python\Hackathons\2022.2 misc\downloads\AllStar'
songList = (glob.glob(baseFolder+"/*.mp3"))

silenceDB = 0 # how many db is silence 0-20


"""
librosa.get_samplerate
    sample rate is the number of samples of audio carried per second, measured in Hz or kHz
    good ~48,000
Short-time Fourier transform (STFT)
    STFT represents a signal in the time-frequency domain by computing discrete Fourier transforms (DFT) over short overlapping windows
    know the amplitude of a given frequency in audio sample(s)
librosa.amplitude_to_db
    translate STFT amplitude to decibels 
    good ~-6db
"""

dfFinal = pd.DataFrame(columns = ['fileName', 'SampleRate', 'feqRange', 'feqMax','feqMin','feqAvg','feqMed','feqStd','FeqSkew','lenSong','maxSilence'                            
                            ])

#E Tests
for SampFile in songList:
    fileName = SampFile[SampFile.rfind("\\")+1:len(SampFile)-4]
    #Test Start
    sampRate = librosa.get_samplerate(SampFile)

    #get frequency Range
    audioData, sr = librosa.load(SampFile, sr=sampRate)
    STFT = np.abs(librosa.stft(audioData))
    Xdb = librosa.amplitude_to_db(abs(STFT))
    feqMax = np.max(Xdb)
    feqMin = np.min(Xdb)
    feqAvg = np.average(Xdb)
    feqMed = np.median(Xdb)
    feqStd = np.std(Xdb)
    feqRange = abs(feqMax) - abs(feqMin)
    feqSkew = abs(feqAvg) - abs(feqMed)

    lenSong = librosa.get_duration(y=audioData, sr=sr)
    
    #The threshold (in decibels) below reference to consider as silence
    nonMuteSections = librosa.effects.split(audioData, top_db = silenceDB)    
    lenList = [0]
    for i in nonMuteSections:
        val=i[1]-i[0]
        lenList.append(val)
    maxSilence = max(lenList)    

    # TODO
        
    #visuals
#    plt.figure(figsize=(14, 5))
#    librosa.display.specshow(Xdb, sr=sampRate, x_axis='time', y_axis='hz')
#    plt.colorbar()

    ## complete, write metrics and print
    df = pd.DataFrame([[fileName,sampRate,feqRange,feqMax,feqMin,feqAvg,feqMed,feqStd,feqSkew,lenSong,maxSilence]])
    df.columns = ['fileName', 'SampleRate', 'feqRange', 'feqMax','feqMin','feqAvg','feqMed','feqStd','FeqSkew','lenSong','maxSilence']    
    dfFinal = pd.concat([df, dfFinal])                       
                      
    print(fileName,'\n   SampleRate:',sampRate, 'feqRange:', round(feqRange,1),'feqMax:', round(feqMax,1), 'feqMin:', round(feqMin,1)
              , 'feqAvg:', round(feqAvg,1) , 'feqMed:', round(feqMed,1), 'feqStd:', round(feqStd,1),'FeqSkew:', round(feqSkew,1), 'SongLength:', round(lenSong,1)
             ,'maxSilence:',maxSilence
         )
    print("--TEST COMPLETE--")

dfFinal = dfFinal.reset_index(drop=True)
dfFinal.to_excel(baseFolder+'\\dataExport.xlsx')
print("file saved")
print("------ALL TESTS COMPLETE------")

-UxD1FObOH4-Smash Mouth - All Star (Instrumental) 
   SampleRate: 44100 feqRange: 13.3 feqMax: 46.6 feqMin: -33.4 feqAvg: -16.6 feqMed: -17.7 feqStd: 16.4 FeqSkew: -1.1 SongLength: 204.1 maxSilence: 512
--TEST COMPLETE--
8gsy8KKjjFI-All Star Live - Smash Mouth 2017 
   SampleRate: 44100 feqRange: 12.5 feqMax: 46.2 feqMin: -33.8 feqAvg: -16.7 feqMed: -18.0 feqStd: 16.4 FeqSkew: -1.2 SongLength: 189.0 maxSilence: 0
--TEST COMPLETE--
8sFXsP71wfA-All Star, but an AI continues the song [OpenAI Jukebox] 
   SampleRate: 44100 feqRange: 12.3 feqMax: 46.1 feqMin: -33.9 feqAvg: -20.4 feqMed: -29.1 feqStd: 16.3 FeqSkew: -8.6 SongLength: 262.9 maxSilence: 0
--TEST COMPLETE--
aT5JaB5agSE-Smash Mouth - All Star (Lyrics) _ BUGG Lyrics 
   SampleRate: 44100 feqRange: 23.6 feqMax: 51.8 feqMin: -28.2 feqAvg: -11.9 feqMed: -12.5 feqStd: 15.6 FeqSkew: -0.6 SongLength: 232.9 maxSilence: 0
--TEST COMPLETE--
fGgOzxg2lRI-'All Star' But It's 24 Cartoon Impressions 
   SampleRate: 44100 feqRange: 23.1 feqMax: 5

In [17]:
## play audio
import IPython.display as ipd
audioFile = r'C:\Lighthouse\Python\Hackathons\2022.2 misc\downloads\Astley\1P5yyeeYF9o-Never Gonna Give You Up Voice Crack.mp3'
audioFile = badVersion
librosa.load(audioFile, sr=None)
ipd.Audio(audioFile)